In [1]:
# !conda install -c tmap tmap

In [1]:
import tmap as tm
import numpy as np
from tqdm.notebook import tqdm
import pandas as pd
from rdkit import Chem
from rdkit.Chem import Descriptors
from scipy import stats
from faerun import Faerun
import json
from matplotlib.colors import LinearSegmentedColormap
from matplotlib.colors import ListedColormap
import matplotlib.pyplot as plt

from joblib import Parallel, delayed
from itertools import islice
from tqdm import tqdm, tqdm_notebook

import torch
import pickle

/home/zhangwei/anaconda3/envs/rxnfp/lib/python3.6/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
df = pd.read_csv('embedding_e_smiles_decoder_edit_mean.csv')
df['dec_out_embedding'] = df['dec_out_embedding'].apply((lambda x: np.array(eval(x))))
df

src  \
0      C(C)(C)CN1CCC(C(=O)NC2=CC3=C(C=C2)N(C)C(SCC2=C...   
1                 C1CCCC2=C1C(=O)N(C1=CC=C(Cl)C=C1F)C2=O   
2      O=C(NCCC(C)N1CCC(NCC2=CC=CC(C)=C2)CC1)C1=C(C)N...   
3      N1(C2=CC=CC=N2)C=C(C2=CC=CC=N2)C=C(C2=C(C#N)C=...   
4                                   CC(C)OC1=CC(N)=CN=C1   
...                                                  ...   
49936           C1(C2CCC3=CC=C4CCN(C(=O)OCC)CCC4=C23)CC1   
49937      N#CC1=CC=CC(C=C2C3=CC=CC=C3CCC3=CC=CC=C23)=C1   
49938  N(O)=CN1C(C2=C(C)ON=C2C)=C(C2=CC=C(O)C=C2)C2=C...   
49939  C1(NCCCO)=NC=CN2C(C3=CC=C(C(=O)NC4CC4)C=C3)=CN...   
49940  C(C1=CC=CC=C1)(C1=CC=CC=C1)(C1=CC=CC=C1)N1CCC(...   

                                                     tgt superclasses  \
0      C(C)(C)CN1CCC(C(=O)!NC2=CC3=C(C=C2)N(C)C(SCC2=...      class_2   
1      C1CCCC2=C1C(=O)!N(C1=CC=C(Cl)C=C1F)!C2=O<[O:1]...      class_4   
2      O=C(NCCC(C)N1CCC(!NCC2=CC=CC(C)=C2)CC1)C1=C(C)...      class_1   
3      N1(C2=CC=CC=N2)C=C(C2=CC=CC=N2)C=C(!C2=C(C#N)C...      class_3   
4                       CC(C)OC1=CC(!N)=CN=C1<[Br:1]><1>      class_9   
...                                                  ...          ...   
49936  C1([~CH]2CCC3=CC=C4CCN(C(=O)OCC)CCC4=C23)CC1<[...      class_9   
49937  N#C!C1=CC=CC(C=C2C3=CC=CC=C3CCC3=CC=CC=C23)=C1...      class_9   
49938  N(O)!CN1C(C2=C(C)ON=C2C)=C(C2=CC=C(O)C=C2)C2=C...      class_9   
49939  C1(NCCCO)=N[~CH]=CN2C(C3=CC=C(C(=O)NC4CC4)C=C3...      class_9   
49940  C(C1=CC=CC=C1)(C1=CC=CC=C1)(C1=CC=CC=C1)N1CCC(...      class_9   

                                       dec_out_embedding  \
0      [0.29571983218193054, -0.9018130302429199, -0....   
1      [0.2566986680030823, -1.0805777311325073, -1.2...   
2      [0.5655394196510315, -1.205611228942871, -0.58...   
3      [0.33296483755111694, -0.4180213510990143, 0.2...   
4      [0.6703359484672546, -1.1963918209075928, -1.2...   
...                                                  ...   
49936  [0.2359829992055893, -0.4466697871685028, -0.4...   
49937  [0.11196780204772949, -1.2303601503372192, -0....   
49938  [0.7221323251724243, -1.666900634765625, -0.88...   
49939  [0.4220900237560272, -1.152279257774353, -1.00...   
49940  [0.5413049459457397, 0.2613595724105835, -0.77...   

                                                e_smiles  \
0      C(C)(C)CN1CCC(C(=O)NC2=CC3=C(C=C2)N(C)C(SCC2=C...   
1      C1CCCC2=C1C(=O)N(C1=CC=C(Cl)C=C1F)C2=O>>>C1CCC...   
2      O=C(NCCC(C)N1CCC(NCC2=CC=CC(C)=C2)CC1)C1=C(C)N...   
3      N1(C2=CC=CC=N2)C=C(C2=CC=CC=N2)C=C(C2=C(C#N)C=...   
4      CC(C)OC1=CC(N)=CN=C1>>>CC(C)OC1=CC(!N)=CN=C1<[...   
...                                                  ...   
49936  C1(C2CCC3=CC=C4CCN(C(=O)OCC)CCC4=C23)CC1>>>C1(...   
49937  N#CC1=CC=CC(C=C2C3=CC=CC=C3CCC3=CC=CC=C23)=C1>...   
49938  N(O)=CN1C(C2=C(C)ON=C2C)=C(C2=CC=C(O)C=C2)C2=C...   
49939  C1(NCCCO)=NC=CN2C(C3=CC=C(C(=O)NC4CC4)C=C3)=CN...   
49940  C(C1=CC=CC=C1)(C1=CC=CC=C1)(C1=CC=CC=C1)N1CCC(...   

                                                     rxn  class  
0      CCCCOCCOc1ccc(-c2ccc3c(c2)C=C(C(=O)O)CCN3CC(C)...      2  
1      Nc1ccc(Cl)cc1F.O=C1OC(=O)C2=C1CCCC2>>C1CCCC2=C...      4  
2      Cc1cccc(CN)c1.Cc1ncnc(C)c1C(=O)NCCC(C)N1CCC(=O...      1  
3      N#Cc1ccccc1B1OC=CC(C(=O)[O-])O1.O=c1c(Br)cc(-c...      3  
4        CC(C)Oc1cncc(Br)c1.[NH4+]>>CC(C)OC1=CC(N)=CN=C1      9  
...                                                  ...    ...  
49936  CCOC(=O)N1CCc2ccc3c(c2CC1)C(O)(C1CC1)CC3>>C1(C...      9  
49937  Brc1cccc(C=C2c3ccccc3CCc3ccccc32)c1.N#C[Cu]>>N...      9  
49938  Cc1noc(C)c1-c1c(-c2ccc(O)cc2)c2ccccc2n1C=O.NO>...      9  
49939  O=C(NC1CC1)c1ccc(-c2cnc3c(NCCCO)nc(Br)cn23)cc1...      9  
49940  [N-]=[N+]=NCC1CCN(C(c2ccccc2)(c2ccccc2)c2ccccc...      9  

[49941 rows x 7 columns]

### Visualize Embedding by TSne

In [3]:
import re
import numpy as np
import matplotlib.pyplot as plt
from sklearn.manifold import TSNE
from sklearn.metrics import silhouette_score, davies_bouldin_score
%config InlineBackend.figure_format = 'svg'

# tsne
tsne = TSNE(n_components=2, random_state=12) 
vectors = torch.from_numpy(np.stack(df["dec_out_embedding"]))
vectors_tsne = tsne.fit_transform(vectors)

# Get unique labels
label_list = [c for c in df['superclasses']]
unique_labels = np.unique(label_list)

# custom a sort function to sort class_1, class_2, ..., class_10
def custom_sort(label):
    match = re.match(r"([a-z]+)_([0-9]+)", label, re.I)
    if match:
        items = match.groups()
        return (int(items[1]), items[0])
    else:
        return (0, label)

unique_labels = sorted(unique_labels, key=custom_sort)

In [7]:
import matplotlib.pyplot as plt
import matplotlib.text as mtext

# Define color list
color_list = [ 'lightgreen', 'mediumturquoise', 'cadetblue',  'crimson', 'lightcoral', 'plum',  '#bababa', 'blueviolet',  'mediumblue', 'khaki',] 

plt.figure(figsize=(7, 6))

# For each label, create a scatter plot
for i, label in enumerate(unique_labels):
    idx = np.where(np.array(label_list) == label)  # get the indices of the current label
    plt.scatter(vectors_tsne[idx, 0], vectors_tsne[idx, 1], label=str(label), color=color_list[i], s=0.5, alpha = 1)

plt.xticks([])
plt.yticks([])

for spine in plt.gca().spines.values():
    spine.set_visible(False)
    
plt.tight_layout()
plt.show()

### Calculate Cluster Metrics

In [3]:
import torch
vectors = torch.from_numpy(np.stack(df["dec_out_embedding"]))
label_list = [int(c) for c in (df['class'])]

print(vectors.shape)
print(len(label_list))

torch.Size([49941, 256])
49941


In [5]:
# Inner Metric (Davies-Bouldin Index)
from sklearn.cluster import KMeans
from sklearn.metrics import davies_bouldin_score

n_clusters = 10

# Cluster by KMeans
kmeans = KMeans(n_clusters=n_clusters, random_state=42, n_init=10)
y_pred = kmeans.fit_predict(vectors)

# Calculate Metrics
db_index = davies_bouldin_score(vectors, y_pred)
print("Davies-Bouldin Index: ", db_index)

Davies-Bouldin Index:  1.90805176973694


In [6]:
# Inner Metric (Davies-Bouldin Index)
from sklearn.mixture  import GaussianMixture
from sklearn.metrics import davies_bouldin_score

n_clusters = 10

# Cluster by GaussianMixture
gmm = GaussianMixture(n_components=10, random_state=42, n_init=10)
gmm.fit(vectors)
y_pred = gmm.predict(vectors)

# Calculate Metrics
db_index = davies_bouldin_score(vectors, y_pred)
print("Davies-Bouldin Index: ", db_index)

Davies-Bouldin Index:  2.1663937786679712


In [7]:
# Outer Metriscs (purity, ARI, AMI, FMI)
from sklearn.cluster import KMeans
from sklearn.metrics import confusion_matrix, adjusted_rand_score, adjusted_mutual_info_score, fowlkes_mallows_score
import numpy as np

n_clusters = 10

# Cluster by KMeans
kmeans = KMeans(n_clusters=n_clusters, random_state=42, n_init=10)
y_pred = kmeans.fit_predict(vectors)
y_true = label_list

# Calculate Metrics
def calculate_purity(y_true, y_pred):
    confusion_matrix_result = confusion_matrix(y_true, y_pred)
    return np.sum(np.amax(confusion_matrix_result, axis=0)) / np.sum(confusion_matrix_result)

purity = calculate_purity(y_true, y_pred)
ari_score = adjusted_rand_score(y_true, y_pred)
adjusted_mi = adjusted_mutual_info_score(y_true, y_pred)
fmi = fowlkes_mallows_score(y_true, y_pred)

print("Purity: ", purity)
print("Adjusted Rand Inde (ARI): ", ari_score)
print("Adjusted Mutual Information (AMI):", adjusted_mi)
print("Fowlkes-Mallows Index (FMI):", fmi)

Purity:  0.6092989727878897
Adjusted Rand Inde (ARI):  0.2689660060511565
Adjusted Mutual Information (AMI): 0.4190543480149784
Fowlkes-Mallows Index (FMI): 0.40242413575573244


In [8]:
# Outer Metriscs (purity, ARI, AMI, FMI)

from sklearn.mixture  import GaussianMixture
from sklearn.metrics import adjusted_rand_score
import numpy as np

# Cluster by GaussianMixture
gmm = GaussianMixture(n_components=10, random_state=42, n_init=10)
gmm.fit(vectors)
y_pred = gmm.predict(vectors)

# Calculate Metrics
ari_score = adjusted_rand_score(y_true, y_pred)
purity = calculate_purity(y_true, y_pred)
adjusted_mi = adjusted_mutual_info_score(y_true, y_pred)
fmi = fowlkes_mallows_score(y_true, y_pred)

print("Purity: ", purity)
print("Adjusted Rand Inde (ARI): ", ari_score)
print("Adjusted Mutual Information (AMI):", adjusted_mi)
print("Fowlkes-Mallows Index (FMI):", fmi)

Purity:  0.7099377265172904
Adjusted Rand Inde (ARI):  0.33217268612738815
Adjusted Mutual Information (AMI): 0.48859896162406463
Fowlkes-Mallows Index (FMI): 0.44673677213267166
